In [31]:
from bs4 import BeautifulSoup
import requests
import requests.exceptions
from urllib.parse import urlsplit
from collections import deque
import re

#list of websites
new_urls = deque(['https://www.nj.com/south/', 'https://www.theclarionnews.com/', 'https://www.inquirer.com/', 
                  'https://triblive.com/', 'https://www.nj.com/starledger/', 'https://www.northjersey.com/', 
                  'https://www.nj.com/times/', 'https://www.topuniversities.com/', 
                  'https://www.collegeraptor.com/find-colleges/articles/2023-university-rankings/', 
                  'https://www.timeshighereducation.com/world-university-rankings', 'https://www.collegefactual.com/rankings/',
                 'https://nj.gov/state/nonprofit.shtml', 'https://www.irs.gov/charities-and-nonprofits', 
                  'https://njnonprofits.org/njnonprofitcom/', 'https://www.state.nj.us/treasury/taxation/rsb100.shtml',
                 'https://charity.lovetoknow.com/List_of_Nonprofit_Organizations', 'https://greatnonprofits.org/state/New%20Jersey',
                 'https://www.councilofnonprofits.org/what-is-a-nonprofit', 'https://www.guidestar.org/', 'https://www.morrischamber.org/nonprofit-organizations.html',
                 'https://www.historians.org/', 'https://www.oah.org/resources/scholarship/u.s-history-organizations/', 'https://www.whitehousehistory.org/',
                 'https://www.bestmastersdegrees.com/lists/5-great-professional-organizations-for-history-majors', 'https://www.thewha.org/', 
                 'https://hbr.org/2012/12/your-companys-history-as-a-leadership-tool', 'https://history.osu.edu/careers/professional-organizations',
                 'https://www.historians.org/about-aha-and-membership/affiliated-societies', 'https://www.oah.org/', 'https://link.springer.com/referenceworkentry/10.1007/978-3-319-31816-5_1-1',
                 'https://byjus.com/free-ias-prep/important-organizations-and-founders/', 'https://www.oliveboard.in/blog/history-study-material-list-organisations-founders/', 
                 'https://sourcebooks.fordham.edu/mod/1820fourier.asp', 'https://www.universiteitleiden.nl/en/research/research-projects/humanities/the-promise-of-organization.-political-associations-1820-1890-debate-and-practice',
                 'https://nj.gov/', 'https://www.njcourts.gov/', 'https://www.state.nj.us/treasury/taxation/', 'https://www.njtransit.com/', 'https://www.nj.com/',
                 'https://visitnj.org/', 'https://www.njconsumeraffairs.gov/', 'https://www.njeda.com/', 'https://www.rutgers.edu/', 'https://www.ramapo.edu/', 'https://www.njoag.gov/',
                 'https://tcnj.edu/', 'https://www.panynj.gov/port-authority/en/index.html', 'https://www.pa.gov/', 'https://www.upenn.edu/', 'https://www.psu.edu/', 'https://www.visitpa.com/', 'https://www.calu.edu/', 'https://www.paturnpike.com/',
                 'https://www.phila.gov/', 'https://www.legis.state.pa.us/', 'https://www.patreasury.gov/', 'https://www.kutztown.edu/', 'https://www.pct.edu/', 'https://www.iup.edu/', 'https://www.wcupa.edu/', 
                 'https://www.palottery.state.pa.us/', 'https://www.attorneygeneral.gov/', 'https://high-schools.com/directory/nj/', 'https://www.education.pa.gov/Schools/Pages/Public-Schools.aspx', 'https://high-schools.com/directory/pa/'
                 ])

# list of website processed
processed_urls = set()

# alist of obtained emails
emails = set()


max_email_size = 10000

max_connect_timeout = 100
max_read_timeout = 600

file_container = open('HPTF2.txt','a+') #save into text file, mode is a+ for reading and writing

email_dict = {} #create a dictionary for emails


try:
    while len(new_urls) and len(emails)<max_email_size:
    
    
    
        print(f"Collected emails: {len(emails)}")  
    
        url = new_urls.popleft()
        processed_urls.add(url)

        parts = urlsplit(url)
        base_url = "{0.scheme}://{0.netloc}".format(parts)
        path = url[:url.rfind('/')+1] if '/' in parts.path else url

        print("Processing %s" % url)
        try:
            response = requests.get(url, timeout = (max_connect_timeout, max_read_timeout))
        except (requests.exceptions.MissingSchema, 
                requests.exceptions.ConnectionError,
                requests.exceptions.Timeout,
                requests.exceptions.InvalidURL,
                requests.exceptions.TooManyRedirects):
            continue

        new_emails = set(re.findall(r"[a-z0-9\.\-+_]+@[a-z0-9\.\-+_]+\.[a-z]+", response.text, re.I))
        
        
        
        
        filter_new_emails = set([])
        
 
        for i in new_emails: #check for repeated emails
            if i not in emails:
                filter_new_emails.add(i)
        file_container.write("\n" + str(filter_new_emails)) #save newest collected emails into txt file

        
        emails.update(filter_new_emails)
   
        
    
        #redirecting to new links
    
        soup = BeautifulSoup(response.text)

        for anchor in soup.find_all("a"):
            link = anchor.attrs["href"] if "href" in anchor.attrs else ''
            if link.startswith('/'):
                link = base_url + link
            elif not link.startswith('http'):
                link = path + link
            if not link in new_urls and not link in processed_urls:
                new_urls.append(link)
        
except Exception as e:
    print("Error: {}".format(e))
    file_container.close()
    
    

for itr_emails in emails:   #iterate through all the emails collected
            
    suffix = itr_emails.split("@",1)[1]   #split the email from @
    
    if suffix not in email_dict.keys():   #if the suffix is new
        email_dict[suffix] = set()     #create a new key for the suffix
    
    email_dict[suffix].add(itr_emails)  #add the email to the corresponding suffix
    
print("this is email_dict" + "\n")
print(email_dict)
print("\n")


spread_sheet_list = set([]) #this is the set to export to the google spreadsheet
        
for gmail_keys in email_dict.keys(): #check if the key is gmail
    
    if gmail_keys != "gmail.com": #if not, then loop through the value sets to get the emails
        
        for collected_email_list in email_dict.values(): # loop through all the value in the dictionary, returns lists
            
            if len(collected_email_list) < 51: # if the length of this set is less than 51
                
                for collected_emails in collected_email_list: # loop through every single value set, are emails
                    
                    spread_sheet_list.add(collected_emails)
                        
                
            else:   # if the length is greater than 50
                     
                email_list = list(collected_email_list)
                
                for actually_emails in email_list:  #returns emails    
                    
                    if actually_emails != email_list[50]: #get 50 emails for each suffix
                            
                        spread_sheet_list.add(actually_emails) #add the collected email to a set
                
                    else: # when the length reaches 50
                        
                        break  #break the loop
        
    else:   #if the suffix is gmail.com
        
        for j in email_dict.values(): #returns a list of emails
            
            for itr_email in j: #returns email
                
                spread_sheet_list.add(itr_email)  #add the email to the list
            

print("\n" + "this is spread_sheet_list"+"\n")
print(spread_sheet_list)

Collected emails: 0
Processing https://www.nj.com/south/
Collected emails: 43
Processing https://www.theclarionnews.com/
Collected emails: 44
Processing https://www.inquirer.com/
Collected emails: 63
Processing https://triblive.com/
Collected emails: 63
Processing https://www.nj.com/starledger/
Collected emails: 111
Processing https://www.northjersey.com/
Collected emails: 111
Processing https://www.nj.com/times/
Collected emails: 130
Processing https://www.topuniversities.com/
Collected emails: 130
Processing https://www.collegeraptor.com/find-colleges/articles/2023-university-rankings/
Collected emails: 130
Processing https://www.timeshighereducation.com/world-university-rankings
Collected emails: 130
Processing https://www.collegefactual.com/rankings/
Collected emails: 130
Processing https://nj.gov/state/nonprofit.shtml
Collected emails: 131
Processing https://www.irs.gov/charities-and-nonprofits
Collected emails: 131
Processing https://njnonprofits.org/njnonprofitcom/
Collected ema

In [34]:
print(len(spread_sheet_list))

10677
